In [1]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer

In [2]:
path = '../archive/anime_with_synopsis.csv'
df = pd.read_csv(path)

In [3]:
df.rename(columns={"sypnopsis" : "Synopsis"}, inplace=True)

In [4]:
df.sample(10)

MAL_ID                                               Name    Score  \
1952     2248  Naruto: Dai Katsugeki!! Yuki Hime Shinobu Houj...     6.87   
8051    23881                                 Momon's Sand Witch  Unknown   
15960   43756                                          Bakuten!!  Unknown   
1165     1317             Eyeshield 21: Maboroshi no Golden Bowl     6.67   
6076    13249                                         Lupin VIII     5.58   
5674    11113                                Usagi Drop Specials     7.98   
5623    10923          Tantei Opera Milky Holmes: Summer Special     6.98   
13864   38770  Detective Conan Movie 23: The Fist of Blue Sap...     7.82   
15368   41496                                         Koi Nobori  Unknown   
6495    16163       Sore Ike! Anpanman: Kirakira Boshi no Namida  Unknown   

                                                  Genres  \
1952   Action, Comedy, Sports, Martial Arts, Fantasy,...   
8051                                        Comedy, Kids   
15960                                             Sports   
1165                                     Sports, Shounen   
6076                          Adventure, Comedy, Shounen   
5674                                Josei, Slice of Life   
5623                        Comedy, Mystery, Super Power   
13864    Action, Mystery, Comedy, Police, Drama, Shounen   
15368                               Action, Drama, Music   
6495                Kids, Adventure, Comedy, Super Power   

                                                Synopsis  
1952   The genin of Konoha are having a sports day fi...  
8051   omon and her pet Tanu have been close friends ...  
15960  The story follows Shoutarou Futaba, a boy who'...  
1165   The Uraharajuku Boarders may have been knocked...  
6076   Pilot of Lupin sequel included with the Lupin ...  
5674   Four short episodes bundled with DVD/Blu-Ray. ...  
5623   special program of Tantei Opera Milky Holmes p...  
13864                        23rd Detective Conan Movie.  
15368  usic video directed by Mitsuyuki Ishibashi and...  
6495   panman helps the princess Nandananda to find t...

In [5]:
df['Synopsis'] = df['Synopsis'].fillna('')

In [6]:
docs = []
for i in range(len(df)):
    docs.append(df['Synopsis'][i])


In [7]:
vec = CountVectorizer(stop_words='english')
X = vec.fit_transform(docs)
count_df = pd.DataFrame(X.toarray(), columns=vec.get_feature_names_out())
count_df.sample(10)

00  000  000th  001  0015  002  003  0060  0068  007  ...  青青草原  飯野真澄  \
1626    0    0      0    0     0    0    0     0     0    0  ...     0     0   
15122   0    0      0    0     0    0    0     0     0    0  ...     0     0   
12166   0    0      0    0     0    0    0     0     0    0  ...     0     0   
13616   0    0      0    0     0    0    0     0     0    0  ...     0     0   
12882   0    0      0    0     0    0    0     0     0    0  ...     0     0   
12462   0    0      0    0     0    0    0     0     0    0  ...     0     0   
2048    0    0      0    0     0    0    0     0     0    0  ...     0     0   
7140    0    0      0    0     0    0    0     0     0    0  ...     0     0   
5028    0    0      0    0     0    0    0     0     0    0  ...     0     0   
14142   0    0      0    0     0    0    0     0     0    0  ...     0     0   

       高河  鳥羽和一  鶺鴒余暇  鶺鴒診断  麻城ゆう  黄色いしあわせ  박사  카프  
1626    0     0     0     0     0        0   0   0  
15122   0     0     0     0     0        0   0   0  
12166   0     0     0     0     0        0   0   0  
13616   0     0     0     0     0        0   0   0  
12882   0     0     0     0     0        0   0   0  
12462   0     0     0     0     0        0   0   0  
2048    0     0     0     0     0        0   0   0  
7140    0     0     0     0     0        0   0   0  
5028    0     0     0     0     0        0   0   0  
14142   0     0     0     0     0        0   0   0  

[10 rows x 45064 columns]

In [8]:
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\35191\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

### Cleaning up and tokenizing text lmao xd

In [9]:
from nltk.tokenize import word_tokenize
def tokenize(text):
    words = word_tokenize(text)
    words = [w.lower() for w in words]
    words = [w for w in words if w not in stopwords.words('english')]
    return words
    

### Building the inverted index

In [10]:
def build_inverted_index(words):
    inverted = {}
    for index, word in enumerate(words):
        locations = inverted.setdefault(word, [])
        locations.append(index)
    return inverted

def inverted_index_add(inverted, doc_id, doc_index):
    for word in doc_index.keys():
        locations = doc_index[word]
        indices = inverted.setdefault(word, {})
        indices[doc_id] = locations
    return inverted

In [11]:
df.head()

MAL_ID                             Name Score  \
0       1                     Cowboy Bebop  8.78   
1       5  Cowboy Bebop: Tengoku no Tobira  8.39   
2       6                           Trigun  8.24   
3       7               Witch Hunter Robin  7.27   
4       8                   Bouken Ou Beet  6.98   

                                              Genres  \
0    Action, Adventure, Comedy, Drama, Sci-Fi, Space   
1              Action, Drama, Mystery, Sci-Fi, Space   
2  Action, Sci-Fi, Adventure, Comedy, Drama, Shounen   
3  Action, Mystery, Police, Supernatural, Drama, ...   
4          Adventure, Fantasy, Shounen, Supernatural   

                                            Synopsis  
0  In the year 2071, humanity has colonized sever...  
1  other day, another bounty—such is the life of ...  
2  Vash the Stampede is the man with a $$60,000,0...  
3  ches are individuals with special powers like ...  
4  It is the dark century and the people are suff...

In [12]:
import tqdm

In [13]:
inverted_doc_indexes = {}
files_with_index = []
files_with_tokens = {}

doc_id = 0

for anime in df['Name']:
    words = tokenize(df['Synopsis'][doc_id])
    files_with_tokens[doc_id] = words
    doc_index = build_inverted_index(words)
    inverted_index_add(inverted_doc_indexes, doc_id, doc_index)
    files_with_index.append(doc_id)
    doc_id += 1


In [14]:
#import reduce
from functools import reduce
# def boolean_search(inverted, animes, query):
#     query_words = tokenize(query)
#     query_words = [w for w in query_words if w in inverted.keys()]
#     if len(query_words) == 0:
#         return []
#     result = inverted[query_words[0]]
#     for word in query_words[1:]:
#         result = result.intersection(inverted[word])
#     return [animes[doc_id] for doc_id in result]
def boolean_search(inverted, animes, query):
    words = [word for _, word in enumerate(tokenize(query)) if word in inverted]
    results = [set(inverted[word].keys()) for word in words]
    docs = reduce(lambda x, y: x & y, results) if results else []
    return [animes[doc_id] for doc_id in docs]

In [15]:
print(boolean_search(inverted_doc_indexes, df['Name'], 'cool anime about vikings'))

[]


In [16]:
DF = {}
for word in inverted_doc_indexes.keys():
    DF[word] = len([doc for doc in inverted_doc_indexes[word]])

total_vocab_size = len(DF)
total_vocab_size

52360

In [17]:
#import COunter
from collections import Counter

In [18]:
files_with_tokens.items()

dict_items([(0, ['year', '2071', ',', 'humanity', 'colonized', 'several', 'planets', 'moons', 'solar', 'system', 'leaving', 'uninhabitable', 'surface', 'planet', 'earth', 'behind', '.', 'inter', 'solar', 'system', 'police', 'attempts', 'keep', 'peace', 'galaxy', ',', 'aided', 'part', 'outlaw', 'bounty', 'hunters', ',', 'referred', '``', 'cowboys', '.', "''", 'ragtag', 'team', 'aboard', 'spaceship', 'bebop', 'two', 'individuals', '.', 'mellow', 'carefree', 'spike', 'spiegel', 'balanced', 'boisterous', ',', 'pragmatic', 'partner', 'jet', 'black', 'pair', 'makes', 'living', 'chasing', 'bounties', 'collecting', 'rewards', '.', 'thrown', 'course', 'addition', 'new', 'members', 'meet', 'travels—ein', ',', 'genetically', 'engineered', ',', 'highly', 'intelligent', 'welsh', 'corgi', ';', 'femme', 'fatale', 'faye', 'valentine', ',', 'enigmatic', 'trickster', 'memory', 'loss', ';', 'strange', 'computer', 'whiz', 'kid', 'edward', 'wong—the', 'crew', 'embarks', 'thrilling', 'adventures', 'unravel'

In [19]:
tf_idf = {}

N = len(files_with_tokens)
for doc_id, tokens in files_with_tokens.items():
    counter = Counter(tokens)
    words_count = len(tokens)

    for token in np.unique(tokens):
        tf = counter[token]
        tf = 1 + np.log(tf)

        if token in DF:
            df = DF[token]
        else:
            df = 0
        idf = np.log((N + 1) / (df + 1))
        tf_idf[doc_id, token] = tf * idf

In [20]:
def ranked_search(k, tf_idf_index, animes, query):
    tokens = tokenize(query)
    query_weights = {}

    for doc_id, token in tf_idf:
        if token in tokens:
            query_weights[doc_id] = query_weights.get(doc_id, 0) + tf_idf_index[doc_id, token]
    
    query_weights = sorted(query_weights.items(), key = lambda x : x[1], reverse=True)
    results = []
    for i in query_weights[:k]:
        results.append(animes[i[0]])
    return results

In [27]:
new_df = pd.read_csv(path)
print(ranked_search(10, tf_idf, new_df['Name'], 'sagiri izumi'))

['Eromanga-sensei', 'Eromanga-sensei OVA', 'Zetsuai 1989', 'Love Stage!!', 'A3! Season Spring & Summer', 'Psycho-Pass: Sinners of the System Case.1 - Tsumi to Bachi', 'Mama wa Shougaku 4 Nensei', 'Bronze: Zetsuai Since 1989', 'Kidou Keisatsu Patlabor', 'Okusama ga Seitokaichou!+!']
